# Descente de Gradient 

### Introduction

Nous allons mettre en pratique nos connaissances sur la descente de gradient. Pour cela, nous utiliserons nos données d'entraînement provenant de l'ensemble de données sur le cancer du sein de l'Université du Wisconsin disponibles en ligne.

In [ ]:
import pandas as pd
df = pd.read_csv('./cell_data.csv')
df[:3]

Si nous examinons les données, nous constatons que nous avons 569 observations, et que chaque observation présente les caractéristiques `surface_moyenne` et `concavite_moyenne` ainsi qu'une cible, c'est-à-dire le résultat de l'observation qui a fini par être cancéreuse ou non. Pour cette leçon, nous ne nous entraînerons que sur la caractéristique `surface_moyenne`

In [ ]:
df.shape

## Hypothèse 

Comme nous le savons, notre objectif est de trouver une fonction d'hypothèse qui puisse utiliser les caractéristiques ci-dessus pour prédire la cible. Écrivons d'abord la forme de notre fonction d'hypothèse qui ne considère que la zone cellulaire. Notre fonction d'hypothèse prend la forme :

* $z(x) = w_1*cell\_area + b$
* $a(z) = \frac{1}{1 + e^{-z}}$

Nous voudrons trouver les paramètres `w_1` et `b` qui minimisent la fonction de coût pour nos données d'entraînement.

### Mise en oeuvre


Commençons par traduire le composant linéaire de notre fonction d'hypothèse en code.

**Question** : Compléter le code suivant

In [ ]:
def linear_component(w1, b, cell_area):
    pass

Dans notre fonction, nous aurons nos paramètres, $w_1$ ​ et $b$ comme arguments. Cela nous permettra de tester plus facilement différents paramètres pour notre fonction d'hypothèse

Vérifions notre travail avec différents paramètres.

In [ ]:
w1 = .03
b = -1
linear_component(w1, b, 1.001)
# -0.96997

In [ ]:
w1 = .04
b = -.5
linear_component(w1, b, 1.001)
# 2.039

Ainsi, nous pouvons constater qu'en ajustant nos paramètres, nous obtenons différentes valeurs de sortie pour la même observation. L'objectif est d'ajuster les paramètres de manière à ce que, lorsque nous alimentons la valeur de retour de notre composant linéaire à la couche d'activation, elle se rapproche des valeurs observées dans les données d'entraînement.

**Question** :  Compléter l'implémentation de la fonction `sigmoid` function.

In [ ]:
import numpy as np
def sigmoid(z):
    return 1/(1 + np.exp(-z))

In [ ]:
first_area = 1001.0
z = linear_component(.03, -2, 1.001)
sigmoid(z)
# 0.12239

In [ ]:
df[:1]

Si nous examinons la première observation, nous constatons que notre prédiction de 0,88 n'est pas très performante pour prédire une valeur observée de 0. Mais ce n'est pas grave, nous n'avons pas encore entraîné notre fonction d'hypothèse.








### La fonction coût

En fait, nous n'avons même pas encore évalué nos paramètres sur l'ensemble des données d'entraînement. Écrivons notre fonction de coût afin de pouvoir le faire.

$J(\theta) = SSE(w, b) = \sum_{i = 1}^n (y_i - h(x_i))^2 = \sum_{i = 1}^n (y_i - \sigma(z(w, b, x_i)))^2$

On décompose la fonction ci dessus en bloc :

Commençons par la gauche, nous avons une fonction de coût $J$, dont la sortie change lorsque nous modifions les valeurs de nos paramètres, $\theta$. Le coût est la somme des erreurs quadratiques, $SSE$, dont la sortie dépend des deux paramètres $w$ et $b$.

Ensuite, nous voyons $\sum_{i = 0}^n (y_i - h(x_i))^2$ qui est la formule pour SSE. Le terme $\sum$ signifie qu'il faut parcourir chaque observation, de la première à la dernière (i = 1 à $n$ observations), et additionner la différence entre ce qui a été observé avec l'observation et ce que la fonction d'hypothèse a prédit, au carré.

### Mise en oeuvre

Avant de poursuivre, combinons les appels de notre composant linéaire et de notre fonction sigmoïde en une fonction appelée `h(w, b, x)`. C'est la fonction d'hypothèse qui dépend de nos paramètres w et b, ainsi que de la valeur de la caractéristique x.

**Question** : compléter la fonction $h$

In [ ]:
def h(w, b, x):
    pass

In [ ]:
h(.03, -2, 1.001)
# 0.12239

**Question** : Passons maintenant à l'écriture du code pour la somme des erreurs quadratiques. Nous le ferons en écrivant d'abord une fonction qui calcule simplement l'erreur quadratique, puis nous nous inquiéterons d'additionner toutes les erreurs.

In [ ]:
def squared_error(w, b, x1, y):
    pass

**Question** : Utilisez les fonctions `linear_component` et `sigmoid` ci-dessous pour calculer l'erreur quadratique.

```python
def linear_component(w1, b, cell_area):
    return w1*cell_area + b

def sigmoid(z):
    return 1/(1 + np.exp(-z))
```

Vérifions les résultats

In [ ]:
w = .3
b = -.5
cell_area = 1.001
y = 0
squared_error(w, b, cell_area, y)
# 0.2027


Maintenant, nous allons utiliser la fonction `squared_error` ci-dessus pour calculer la somme des erreurs quadratiques.

> Ici, nous l'avons fait pour vous. Elle utilise la fonction d'erreur quadratique que vous avez écrite précédemment.


In [ ]:
def sum_of_squared_errors(paired_data, w, b):
    return sum([squared_error(w, b, feature, target) for (feature, target) in paired_data])

In [ ]:
paired_data = df[['surface_moyenne', 'est_cancereux']].to_numpy()

Les données appariées sont une liste d'observations, où chaque élément est une liste avec une caractéristique et une cible

In [ ]:
paired_data[0]


Par exemple, ci-dessus, on voit que notre première observation a une caractéristique de zone cellulaire de 1001 et une cible de 0. 


Notre somme des erreurs quadratiques parcourt toutes les observations, calcule les erreurs quadratiques et les additionne ensuite.

In [ ]:
sum_of_squared_errors(paired_data, .04, -.5)
# 168.10946204835383


Si nous remplaçons nos paramètres $w$ et $b$ par différentes valeurs, nous obtiendrons différentes erreurs quadratiques. Notre objectif est de trouver les paramètres $w$ et $b$ qui minimisent notre SSE. 


### Descending Along a Cost Curve

Maintenant, si nous devions tracer chacune des valeurs potentielles de $w$ et $b$ dans une plage, nous trouverions un coût différent pour chaque combinaison de nos paramètres. Traçons ci-dessous les valeurs de nos paramètres et le coût correspondant.

In [ ]:
import pandas as pd
import plotly.graph_objects as go
url = "https://storage.googleapis.com/curriculum-assets/nn-from-scratch/cost_curve_three_d.json"

fig_dict = dict(pd.read_json(url, typ = 'dict', convert_dates=False))
go.Figure(fig_dict)

Maintenant, l'objectif de la descente de gradient est de descendre le long de la courbe de coût sans avoir à la tracer. La raison en est que, lorsque l'on ajoute plus de paramètres, il devient impossible de tracer une courbe de coût entière. Au lieu de cela, nous descendons le long de la courbe de coût en utilisant la descente de gradient, en prenant des pas dans la direction de la pente la plus forte. Et nous trouvons cette direction en calculant le gradient, c'est-à-dire la dérivée partielle par rapport à chaque paramètre. 


Les dérivées partielles s'écrivent :
$$
  \frac{\partial J}{\partial w} \  \frac{\partial J}{\partial b}
  
$$

C'est-à-dire, le changement de notre courbe de coût par rapport à un changement de notre paramètre w et de notre terme de biais $b$, où notre courbe de coût est la suivante

$J(w, b) = \sum_{i = 1}^n (y_i - \sigma(z(w, b, x_i)))^2$

Le calcul des dérivées partielles pour notre courbe de coût ci-dessus est assez compliqué et implique ce qu'on appelle la règle de la chaîne. Nous aborderons la règle de la chaîne dans de futures leçons, donc pour l'instant, nous allons simplement vous donner les dérivées partielles.

$\frac{\partial J}{\partial w} = \frac{\partial J}{\partial a} \frac{\partial a}{\partial z} \frac{\partial z}{\partial w} = 2(h(x_i) - y_i)*\sigma(z(x))(1 - \sigma(z(x))) * x_i$

$\frac{\partial J}{\partial b} = \frac{\partial J}{\partial a} \frac{\partial a}{\partial z} \frac{\partial z}{\partial b} = 2(h(x_i) - y_i)*\sigma(z(x))(1 - \sigma(z(x))) * 1$

Et nous pouvons transformer ce qui précède en code avec ce qui suit :

In [ ]:
def dj_dw(w, b, x, y):
    return 2*(h(w, b, x) - y)*h(w, b, x)*(1 - h(w, b, x))*x

In [ ]:
def dj_db(w, b, x, y):
    return 2*(h(w, b, x) - y)*h(w, b, x)*(1 - h(w, b, x))*1

"Les deux fonctions ci-dessus nous permettent de déterminer le taux de variation instantané dans chaque direction sur notre courbe de coût. Par exemple, lorsque nous sommes à l'emplacement de notre courbe de coût de $w = .04$ et $b = -.5$, notre taux de variation instantané dans la direction de $w$ est de .18."

In [ ]:
w = .04
b = -.5
y = 0
x = 1.001
dj_dw(w, b, x, y)


En d'autres termes, si nous modifions légèrement notre paramètre $w$, nous nous attendons à ce que notre coût, calculé par notre fonction $J$, change de $.18$.



Donc, comme nous le savons, notre procédure de descente de gradient consiste à mettre à jour nos paramètres de manière répétée en fonction de notre "bang for our buck" (rapport coût-efficacité). C'est-à-dire que nous modifions chaque paramètre en proportion de la quantité dont le changement nous déplacerait vers le minimum de la courbe de coût. Et nous avons calculé ce changement de la courbe de coût par changement du paramètre à travers $\frac{\partial J}{\partial w}$ et $\frac{\partial J}{\partial w}$ ci-dessus. Ok, donc ci-dessous, nous appliquons la descente de gradient en mettant à jour de manière répétée chaque paramètre par sa dérivée partielle respective.



> Choisissez des paramètres initiaux $\theta$ et un taux d'apprentissage $\eta$, puis
>
> Répétez
>
> $\theta =  \theta - \eta *\frac{\partial J}{\partial \theta}$

Le programme correspondant s'écrit

In [ ]:
w = .5
b = .5
eta = .01

for i in range(0, 150):
    for (x, y) in paired_data:
        dj_dw_calc = dj_dw(w, b, x, y)
        dj_db_calc = dj_db(w, b, x, y)
        w += -eta*dj_dw_calc
        b += -eta*dj_db_calc

In [ ]:
w

In [ ]:
b

Ainsi, en mettant à jour de manière répétée nos paramètres de manière à trouver des valeurs qui se rapprochent du minimum de la courbe de coût, nous finissons par obtenir des valeurs de $w = -6.57$ et $b = 4.75$.


> Voyons comment nous avons réussi par rapport à ce que `sklearn`trouve pour nos paramètres

In [ ]:
from sklearn.linear_model import LogisticRegression
log_model = LogisticRegression(fit_intercept=True)

areas = df[['surface_moyenne']]
targets = df['est_cancereux']

log_model.fit(areas, targets)
log_model.coef_

In [ ]:
log_model.intercept_

### Predicting Going Forward

Une fois que nous avons trouvé ces paramètres, nous pouvons les utiliser dans notre fonction d'hypothèse à l'avenir.

Nous avons fait l'hypothèse suivante :


In [ ]:
def h(w, b, x):
    return sigmoid(linear_component(w, b, x))

Une fois que nous avons entraîné notre modèle et déterminé les valeurs optimales des paramètres $w$ et $b$, nous pouvons utiliser ce modèle pour faire des prédictions sur de nouvelles observations.

In [ ]:
selected_obs = df[['surface_moyenne', 'est_cancereux']][17:21]
selected_obs

Nous avons choisi une sélection qui contient à la fois des observations bénignes et cancéreuses.

In [ ]:
observations = selected_obs.to_numpy()
observations

In [ ]:
w = -6.57
b = 4.754
[h(w, b, observation[0]) for observation in observations]

In [ ]:
selected_obs['est_cancereux']

<center>
<a href="https://www.jigsawlabs.io/free" style="position: center"><img src="https://storage.cloud.google.com/curriculum-assets/curriculum-assets.nosync/mom-files/jigsaw-labs.png" width="15%" style="text-align: center"></a>
</center>

### Answers

In [ ]:
def linear_component(w1, b, cell_area):
    return w1*cell_area + b

In [ ]:
def h(w, b, x):
    return sigmoid(linear_component(w, b, x))

In [ ]:
def squared_error(w, b, x1, y):
    return (y - h(w, b, x1))**2